In [1]:
import pandas as pd
import numpy as np
import scipy as sp
from scipy import stats
from scipy.stats import norm, skew
import plotly
import plotly.plotly as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
from plotly import tools
import seaborn as sns
import json
import requests
import warnings
from requests.auth import HTTPBasicAuth

In [49]:
df = pd.read_csv('train.csv', header = 0, index_col = None)

In [50]:
df.head(5)

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0   1          60       RL         65.0     8450   Pave   NaN      Reg   
1   2          20       RL         80.0     9600   Pave   NaN      Reg   
2   3          60       RL         68.0    11250   Pave   NaN      IR1   
3   4          70       RL         60.0     9550   Pave   NaN      IR1   
4   5          60       RL         84.0    14260   Pave   NaN      IR1   

  LandContour Utilities    ...     PoolArea PoolQC Fence MiscFeature MiscVal  \
0         Lvl    AllPub    ...            0    NaN   NaN         NaN       0   
1         Lvl    AllPub    ...            0    NaN   NaN         NaN       0   
2         Lvl    AllPub    ...            0    NaN   NaN         NaN       0   
3         Lvl    AllPub    ...            0    NaN   NaN         NaN       0   
4         Lvl    AllPub    ...            0    NaN   NaN         NaN       0   

  MoSold YrSold  SaleType  SaleCondition  SalePrice  
0      2   2008        WD         Normal     208500  
1      5   2007        WD         Normal     181500  
2      9   2008        WD         Normal     223500  
3      2   2006        WD        Abnorml     140000  
4     12   2008        WD         Normal     250000  

[5 rows x 81 columns]

# 1. Cleaning data

In [51]:
df = df.drop('Alley', axis = 1)

In [52]:
df.head(5)

Id  MSSubClass MSZoning  LotFrontage  LotArea Street LotShape LandContour  \
0   1          60       RL         65.0     8450   Pave      Reg         Lvl   
1   2          20       RL         80.0     9600   Pave      Reg         Lvl   
2   3          60       RL         68.0    11250   Pave      IR1         Lvl   
3   4          70       RL         60.0     9550   Pave      IR1         Lvl   
4   5          60       RL         84.0    14260   Pave      IR1         Lvl   

  Utilities LotConfig    ...     PoolArea PoolQC Fence MiscFeature MiscVal  \
0    AllPub    Inside    ...            0    NaN   NaN         NaN       0   
1    AllPub       FR2    ...            0    NaN   NaN         NaN       0   
2    AllPub    Inside    ...            0    NaN   NaN         NaN       0   
3    AllPub    Corner    ...            0    NaN   NaN         NaN       0   
4    AllPub       FR2    ...            0    NaN   NaN         NaN       0   

  MoSold  YrSold  SaleType  SaleCondition  SalePrice  
0      2    2008        WD         Normal     208500  
1      5    2007        WD         Normal     181500  
2      9    2008        WD         Normal     223500  
3      2    2006        WD        Abnorml     140000  
4     12    2008        WD         Normal     250000  

[5 rows x 80 columns]

In [53]:
# creating mean valaue of LotFrontage
LF_mean = df['LotFrontage'].mean()

In [54]:
# insult mean value every NA of LotFrontage
df.loc[:,'LotFrontage'] = df.loc[:,'LotFrontage'].fillna(LF_mean)

In [55]:
df['BsmtQual'] = df['BsmtQual'].fillna('NA')

In [71]:

   #    Ex Excellent
   #    Gd Good
   #    TA Average/Typical
   #    Fa Fair
   #    Po Poor

In [59]:
df['BsmtQual'] = df['BsmtQual'].replace({'NA': 1, 'Po':2, 'Fa':3, 'TA':4, 'Gd':5, 'Ex':6 })

In [72]:
df['FireplaceQu'] = df['FireplaceQu'].fillna('NA')

In [73]:
df['FireplaceQu'] = df['FireplaceQu'].replace({'NA': 1, 'Po':2, 'Fa':3, 'TA':4, 'Gd':5, 'Ex':6 })

In [76]:
df['PoolQC'] = df['PoolQC'].fillna('NA')

In [77]:
df['PoolQC'] = df['PoolQC'].replace({'NA': 1, 'Po':2, 'Fa':3, 'TA':4, 'Gd':5, 'Ex':6 })

In [81]:
#GdPrv Good Privacy
#MnPrv Minimum Privacy
#GdWo Good Wood
#MnWw Minimum Wood/Wire
#NA No Fence

In [82]:
df['Fence'] = df['Fence'].fillna('NA')

In [86]:
df['Fence'] = df['Fence'].replace({'NA': 1, 'MnWw': 2,'GdWo':3, 'MnPrv':4, 'GdPrv':5})

In [88]:
df = df.drop('MiscFeature', axis=1)

In [96]:
df['GarageType'] = df['GarageType'].fillna('NA')

In [107]:
# both varaiable are highly similar
# df[['GarageYrBlt','YearBuilt']]

In [109]:
# drop column because of similarity to YearBuilt
df = df.drop('GarageYrBlt', 1) 

In [111]:
df['GarageFinish'] = df['GarageFinish'].fillna('NA')

In [112]:
df['GarageFinish'] = df['GarageFinish'].replace({'NA':1, 'Unf':2, 'RFn':3, 'Fin':4})

In [115]:
df['GarageQual'] = df['GarageQual'].fillna('NA')

In [ ]:
df['GarageQual'] = df['GarageQual'].replace({'NA':1, 'Po':2, 'Fa':3, 'TA':4, 'Gd':5, 'Ex':6})

In [119]:
df['GarageCond'] = df['GarageCond'].fillna('NA')

In [120]:
df['GarageCond'] = df['GarageCond'].replace({'NA':1, 'Po':2, 'Fa':3, 'TA':4, 'Gd':5, 'Ex':6})

In [141]:
pd.set_option('max_rows', 1500)

In [131]:
pd.set_option('max_columns', 100)

In [133]:
df['MasVnrType'] = df['MasVnrType'].fillna('None')

In [135]:
df['MasVnrArea'] = df['MasVnrArea'].fillna(0) 

In [145]:
df['Electrical'] = df['Electrical'].fillna('Mix')

In [ ]:
   SBrkr	Standard Circuit Breakers & Romex
       FuseA	Fuse Box over 60 AMP and all Romex wiring (Average)	
       FuseF	60 AMP Fuse Box and mostly Romex wiring (Fair)
       FuseP	60 AMP Fuse Box and mostly knob & tube wiring (poor)
       Mix	Mixed

In [146]:
df['Electrical'] = df['Electrical'].replace({'Mix':1, 'FuseP':2, 'FuseF':3, 'FuseA':4, 'SBrkr':5})

In [148]:
df['BsmtCond'] = df['BsmtCond'].fillna('NA') 

In [149]:
df['BsmtCond'] = df['BsmtCond'].replace({'NA':1, 'Po':2, 'Fa':3, 'TA':4, 'Gd':5, 'Ex':6})

In [150]:
df['BsmtExposure'] = df['BsmtExposure'].fillna('NA')

In [151]:
df['BsmtExposure'] = df['BsmtExposure'].replace({'NA':1, 'No':2, 'Mn':3, 'Av':4, 'Gd':5})

In [152]:
df['BsmtFinType1'] = df['BsmtFinType1'].fillna('NA')

In [153]:
df['BsmtFinType1'] = df['BsmtFinType1'].replace({'NA':1, 'Unf':2, 'LwQ':3, 'Rec':4, 'BLQ':5, 'ALQ':6, 'GLQ':7})

In [155]:
df['BsmtFinType2'] = df['BsmtFinType2'].fillna('NA')

In [156]:
df['BsmtFinType2'] = df['BsmtFinType2'].replace({'NA':1, 'Unf':2, 'LwQ':3, 'Rec':4, 'BLQ':5, 'ALQ':6, 'GLQ':7})

In [160]:
df.isnull().sum()

Id               0
MSSubClass       0
MSZoning         0
LotFrontage      0
LotArea          0
Street           0
LotShape         0
LandContour      0
Utilities        0
LotConfig        0
LandSlope        0
Neighborhood     0
Condition1       0
Condition2       0
BldgType         0
HouseStyle       0
OverallQual      0
OverallCond      0
YearBuilt        0
YearRemodAdd     0
RoofStyle        0
RoofMatl         0
Exterior1st      0
Exterior2nd      0
MasVnrType       0
MasVnrArea       0
ExterQual        0
ExterCond        0
Foundation       0
BsmtQual         0
BsmtCond         0
BsmtExposure     0
BsmtFinType1     0
BsmtFinSF1       0
BsmtFinType2     0
BsmtFinSF2       0
BsmtUnfSF        0
TotalBsmtSF      0
Heating          0
HeatingQC        0
CentralAir       0
Electrical       0
1stFlrSF         0
2ndFlrSF         0
LowQualFinSF     0
GrLivArea        0
BsmtFullBath     0
BsmtHalfBath     0
FullBath         0
HalfBath         0
BedroomAbvGr     0
KitchenAbvGr     0
KitchenQual 

In [139]:
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = (30,30)

In [164]:
df.shape

(1460, 78)

In [165]:
df = df.drop('Id', 1)

In [167]:
df.shape

(1460, 77)

In [169]:
df['MoSold'] = df['MoSold'].replace({1:'Jan', 2:'Feb', 3:'Mar', 4:'Apr', 5:'May', 6:'June', 7:'July', 8:'Aug', 9:'Sept', 10:'Oct', 11:'Nov', 12:'Dec'})

In [176]:
# df.info()
# df.dtype

In [183]:
df

MSSubClass MSZoning  LotFrontage  LotArea Street LotShape LandContour  \
0             60       RL    65.000000     8450   Pave      Reg         Lvl   
1             20       RL    80.000000     9600   Pave      Reg         Lvl   
2             60       RL    68.000000    11250   Pave      IR1         Lvl   
3             70       RL    60.000000     9550   Pave      IR1         Lvl   
4             60       RL    84.000000    14260   Pave      IR1         Lvl   
5             50       RL    85.000000    14115   Pave      IR1         Lvl   
6             20       RL    75.000000    10084   Pave      Reg         Lvl   
7             60       RL    70.049958    10382   Pave      IR1         Lvl   
8             50       RM    51.000000     6120   Pave      Reg         Lvl   
9            190       RL    50.000000     7420   Pave      Reg         Lvl   
10            20       RL    70.000000    11200   Pave      Reg         Lvl   
11            60       RL    85.000000    11924   Pave      IR1         Lvl   
12            20       RL    70.049958    12968   Pave      IR2         Lvl   
13            20       RL    91.000000    10652   Pave      IR1         Lvl   
14            20       RL    70.049958    10920   Pave      IR1         Lvl   
15            45       RM    51.000000     6120   Pave      Reg         Lvl   
16            20       RL    70.049958    11241   Pave      IR1         Lvl   
17            90       RL    72.000000    10791   Pave      Reg         Lvl   
18            20       RL    66.000000    13695   Pave      Reg         Lvl   
19            20       RL    70.000000     7560   Pave      Reg         Lvl   
20            60       RL   101.000000    14215   Pave      IR1         Lvl   
21            45       RM    57.000000     7449   Pave      Reg         Bnk   
22            20       RL    75.000000     9742   Pave      Reg         Lvl   
23           120       RM    44.000000     4224   Pave      Reg         Lvl   
24            20       RL    70.049958     8246   Pave      IR1         Lvl   
25            20       RL   110.000000    14230   Pave      Reg         Lvl   
26            20       RL    60.000000     7200   Pave      Reg         Lvl   
27            20       RL    98.000000    11478   Pave      Reg         Lvl   
28            20       RL    47.000000    16321   Pave      IR1         Lvl   
29            30       RM    60.000000     6324   Pave      IR1         Lvl   
30            70  C (all)    50.000000     8500   Pave      Reg         Lvl   
31            20       RL    70.049958     8544   Pave      IR1         Lvl   
32            20       RL    85.000000    11049   Pave      Reg         Lvl   
33            20       RL    70.000000    10552   Pave      IR1         Lvl   
34           120       RL    60.000000     7313   Pave      Reg         Lvl   
35            60       RL   108.000000    13418   Pave      Reg         Lvl   
36            20       RL   112.000000    10859   Pave      Reg         Lvl   
37            20       RL    74.000000     8532   Pave      Reg         Lvl   
38            20       RL    68.000000     7922   Pave      Reg         Lvl   
39            90       RL    65.000000     6040   Pave      Reg         Lvl   
40            20       RL    84.000000     8658   Pave      Reg         Lvl   
41            20       RL   115.000000    16905   Pave      Reg         Lvl   
42            85       RL    70.049958     9180   Pave      IR1         Lvl   
43            20       RL    70.049958     9200   Pave      IR1         Lvl   
44            20       RL    70.000000     7945   Pave      Reg         Lvl   
45           120       RL    61.000000     7658   Pave      Reg         Lvl   
46            50       RL    48.000000    12822   Pave      IR1         Lvl   
47            20       FV    84.000000    11096   Pave      Reg         Lvl   
48           190       RM    33.000000     4456   Pave      Reg         Lvl   
49            20       RL    66.000000     7742   Pave  

In [184]:
correlations_data = df.corr()['SalePrice'].sort_values()
# correlations_data

In [186]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1460 entries, 0 to 1459
Data columns (total 77 columns):
MSSubClass       1460 non-null int64
MSZoning         1460 non-null object
LotFrontage      1460 non-null float64
LotArea          1460 non-null int64
Street           1460 non-null object
LotShape         1460 non-null object
LandContour      1460 non-null object
Utilities        1460 non-null object
LotConfig        1460 non-null object
LandSlope        1460 non-null object
Neighborhood     1460 non-null object
Condition1       1460 non-null object
Condition2       1460 non-null object
BldgType         1460 non-null object
HouseStyle       1460 non-null object
OverallQual      1460 non-null int64
OverallCond      1460 non-null int64
YearBuilt        1460 non-null int64
YearRemodAdd     1460 non-null int64
RoofStyle        1460 non-null object
RoofMatl         1460 non-null object
Exterior1st      1460 non-null object
Exterior2nd      1460 non-null object
MasVnrType       1460 no